<a href="https://colab.research.google.com/github/Shagun20/CSE508_Winter2023_A2_112/blob/main/Ass_2_Ques_2_final.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd

path = '/content/drive/MyDrive/IR_AssnDatasets_Sem6/BBC News Train.csv'
df = pd.read_csv(path)

In [ ]:
df

ArticleId                                               Text  \
0          1833  worldcom ex-boss launches defence lawyers defe...   
1           154  german business confidence slides german busin...   
2          1101  bbc poll indicates economic gloom citizens in ...   
3          1976  lifestyle  governs mobile choice  faster  bett...   
4           917  enron bosses in $168m payout eighteen former e...   
...         ...                                                ...   
1485        857  double eviction from big brother model caprice...   
1486        325  dj double act revamp chart show dj duo jk and ...   
1487       1590  weak dollar hits reuters revenues at media gro...   
1488       1587  apple ipod family expands market apple has exp...   
1489        538  santy worm makes unwelcome visit thousands of ...   

           Category  
0          business  
1          business  
2          business  
3              tech  
4          business  
...             ...  
1485  entertainment  
1486  entertainment  
1487       business  
1488           tech  
1489           tech  

[1490 rows x 3 columns]

In [ ]:
df=df.iloc[: , 1:]

In [ ]:
df

Text       Category
0     worldcom ex-boss launches defence lawyers defe...       business
1     german business confidence slides german busin...       business
2     bbc poll indicates economic gloom citizens in ...       business
3     lifestyle  governs mobile choice  faster  bett...           tech
4     enron bosses in $168m payout eighteen former e...       business
...                                                 ...            ...
1485  double eviction from big brother model caprice...  entertainment
1486  dj double act revamp chart show dj duo jk and ...  entertainment
1487  weak dollar hits reuters revenues at media gro...       business
1488  apple ipod family expands market apple has exp...           tech
1489  santy worm makes unwelcome visit thousands of ...           tech

[1490 rows x 2 columns]

Naive Bayes works by calculating the probability 
of a document belonging to each category based on the presence 
or absence of each term in the document. The category with the highest 
probability is then assigned to the document.

In [ ]:
df
import nltk
from nltk.corpus import stopwords
nltk.download('punkt')
import string


nltk.download('stopwords')
stop_words = set(stopwords.words('english'))
punctuation = set(string.punctuation)



[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [ ]:
def clean(text):

  
  # Remove stop words
  text = ' '.join(word for word in text.split() if word not in stop_words)
    
    # Remove stop words
  text = ' '.join(word for word in text.split() if word not in stop_words)

  text=text.lower()

  return text
    

In [ ]:
def tokenise(text):
 words = nltk.word_tokenize(text)

 return words


In [ ]:
def stem(words):

  stemmer = PorterStemmer()
  stemmed_words = [stemmer.stem(word) for word in words]

  return stemmed_words

In [ ]:
from nltk.stem import PorterStemmer

for index, row in df.iterrows():
  df.at[index,'Text']=stem(tokenise(clean(row['Text'])))


#perform cleaning of text by removing stop words, lower the case
#then the cleaned text is tokenised 
#the tokens are stemmatised


stemmed_data= df
    


In [ ]:
stemmed_data

Text       Category
0     [worldcom, ex-boss, launch, defenc, lawyer, de...       business
1     [german, busi, confid, slide, german, busi, co...       business
2     [bbc, poll, indic, econom, gloom, citizen, maj...       business
3     [lifestyl, govern, mobil, choic, faster, bette...           tech
4     [enron, boss, $, 168m, payout, eighteen, forme...       business
...                                                 ...            ...
1485  [doubl, evict, big, brother, model, capric, ho...  entertainment
1486  [dj, doubl, act, revamp, chart, show, dj, duo,...  entertainment
1487  [weak, dollar, hit, reuter, revenu, media, gro...       business
1488  [appl, ipod, famili, expand, market, appl, exp...           tech
1489  [santi, worm, make, unwelcom, visit, thousand,...           tech

[1490 rows x 2 columns]

Implement the TF-ICF weighting scheme.

In [ ]:
import math
def tf_icf(term, category, tf, class_freq):
  term_freq=0

  if term in tf[category]:
    term_freq=tf[category][term]

  #term_freq stores the term frequency of the term belonging to that class
  #n_t denotes the total number of classes where the term belongs
  n_t= len(class_freq[term])
 # print(n_t, class_freq[term])
  N=5
  #since the total classes that can be there is 5, N is 5

  icf= math.log10(N/n_t)
  #icf is calculated as log( N / CF), where N represents the number of classes, CF is n_t
  # n_t denotes the Number of classes in which that term occurs
  return term_freq*icf

In [ ]:
def tf_icf_calculator(dataset):
  #tf refers to number of times a term occurs in documents of type category

  tf={'business':{}, 'tech':{}, 'politics':{},'sport':{}, 'entertainment':{}  }
# #cretae tf dictionary for all the five classes

#    #iterate throught the dataframes and count the number of occurences of the terms in all documents that belong to that category
  for index, row in dataset.iterrows():
      words= row['Text']
      category= row['Category']
      for word in words:
        if word in tf[category]:
          tf[category][word]+=1
        else:
          tf[category][word]=1

    #tf for all categories have been calculated now

  class_freq={}
  #now class frequency will be found

  for index, row in dataset.iterrows():
    words= row['Text']
    #words is the array of the terms of each row
    category= row['Category']
    #category is the category the document belongs to

    for word in words:
      #for each word in the terms array,
      if word in class_freq:
        if not category in class_freq[word]:
          class_freq[word].append(category)

      else:
        #if word is not in dictionary,
        #initialise a list for that word
        class_freq[word]=[]
        class_freq[word].append(category)

      #class freq is Number of classes in which that term occurs


  #now we have the tf of each term for each category, we create a dictionary of all terms,
  #each term has 5 categories
  categories={'business', 'tech', 'politics', 'sport', 'entertainment'}

  tf_icf_weight={}
  for term in class_freq:
      tf_icf_weight[term]={}
      #now corresponding to each category, tf_icf is found
      for cat in categories:
        tf_icf_weight[term][cat]= tf_icf(term, cat, tf, class_freq)

  return tf_icf_weight







  






    

















Split the BBC train dataset into training and testing sets.

---



In [ ]:
import random

# Set the proportion of data to use for testing
test_proportion = 0.3

df=df.sample(frac=1)

split_index = int(df.shape[0] * test_proportion)

train_data = df[split_index:]
test_data = df[:split_index]




In [ ]:
print(train_data.shape[0]/ df.shape[0])
print(test_data.shape[0]/df.shape[0])


0.7
0.3


Calculate the probability of each category based on the frequency of documents
in the training set that belong to that category.

Train the NB model

In [ ]:
def calculate_categ_wise_prob(dataset):
  categories={'business':0, 'tech':0, 'politics':0, 'sport':0, 'entertainment':0}

  #prob of each categ is defined as the number of documents in category / total number of documents
  for index, row in dataset.iterrows():
    categories[row['Category']]+=1

  for cat in categories:
    categories[cat]/=len(dataset)

  return categories


In [ ]:
def calculate_prob_of_each_term(dataset, tf_icf_terms):
  
  #initialised by 1 so that divide by zero error does not occur
  sum_tf_icf={'business': 1, 'tech':1, 'politics':1, 'sport':1, 'entertainment':1}
  for term in tf_icf_terms:
    for cat in tf_icf_terms[term]:
      sum_tf_icf[cat]+=  tf_icf_terms[term][cat]

  for term in tf_icf_terms:
    for cat in tf_icf_terms[term]:
      tf_icf_terms[term][cat]/= sum_tf_icf[cat]

  return tf_icf_terms




  #prob_of_each_term_given_the categories= tf_icf given the category / sum(tf_icf of the category)+1 
  #1 is added for avoiding 0s and div by 0s




In [ ]:
class NB:

  tf_icf_terms={}
  prob_of_each_category={}
  prob_of_each_term_for_category={}

  def __init__(self, dataset):
    self.tf_icf_terms=tf_icf_calculator(dataset)
    self.prob_of_each_category=calculate_categ_wise_prob(dataset)
    self.prob_of_each_term_for_category = calculate_prob_of_each_term(dataset, self.tf_icf_terms)
    

  def predict(self,terms):

    p_categories={'business':0, 'tech':0, 'politics':0, 'sport':0, 'entertainment':0}
    

    #each probability refers to p(cat_i|x)=p(x1|cat_i).p(x2|cat_i)..p(xn|cat_i)p(cat_i)/(p(x1).p(x2)..p(xn))
    #here since comparison is being performed only, denominator can be ignored
    max=0
    ans=""
    for cat in p_categories:
      p=0
      for term in terms:
        #for simple reasons
        a1=0
        if term in self.prob_of_each_term_for_category:
          a1=math.log(1+self.prob_of_each_term_for_category[term][cat])

        p=p+a1

      p=p+ math.log(1+self.prob_of_each_category[cat])

      if max==0:
        max=p
        ans=cat

      if p>max:
        max=p
        ans=cat
    
    return ans


    #for all the terms 






In [ ]:
#Training the Naive Bayes classifier with TF-ICF:
nb_classifier = NB(train_data)


In [ ]:
print(nb_classifier.tf_icf_terms)



{'redford': {'sport': 0.0, 'entertainment': 0.0009666736503790071, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'vision': {'sport': 0.0, 'entertainment': 0.0001534081142919586, 'politics': 0.00018642964392275529, 'business': 0.0, 'tech': 0.0004061054012022418}, 'sundanc': {'sport': 0.0, 'entertainment': 0.0012083420629737589, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'despit': {'sport': 0.0, 'entertainment': 0.0, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'sport': {'sport': 0.0, 'entertainment': 0.0, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'corduroy': {'sport': 0.0, 'entertainment': 0.00012083420629737589, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'cap': {'sport': 0.0, 'entertainment': 0.0, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'pull': {'sport': 0.0, 'entertainment': 0.0, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'low': {'sport': 0.0, 'entertainment': 0.0, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'face': {'sport': 0.0, 'entertainment':

In [ ]:
print(nb_classifier.prob_of_each_category)


{'business': 0.22818791946308725, 'tech': 0.17641418983700863, 'politics': 0.17737296260786195, 'sport': 0.24065196548418025, 'entertainment': 0.17737296260786195}


In [ ]:
print(nb_classifier.prob_of_each_term_for_category)

{'redford': {'sport': 0.0, 'entertainment': 0.0009666736503790071, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'vision': {'sport': 0.0, 'entertainment': 0.0001534081142919586, 'politics': 0.00018642964392275529, 'business': 0.0, 'tech': 0.0004061054012022418}, 'sundanc': {'sport': 0.0, 'entertainment': 0.0012083420629737589, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'despit': {'sport': 0.0, 'entertainment': 0.0, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'sport': {'sport': 0.0, 'entertainment': 0.0, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'corduroy': {'sport': 0.0, 'entertainment': 0.00012083420629737589, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'cap': {'sport': 0.0, 'entertainment': 0.0, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'pull': {'sport': 0.0, 'entertainment': 0.0, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'low': {'sport': 0.0, 'entertainment': 0.0, 'politics': 0.0, 'business': 0.0, 'tech': 0.0}, 'face': {'sport': 0.0, 'entertainment':

Classify each document in the testing set and compare the predicted category
with the actual category.

In [ ]:
#Use the testing set to evaluate the performance of the classifier.
y_true=[]
y_pred=[]

for index, row in test_data.iterrows():
  y_true.append(row['Category'])
  terms=row['Text']
  y_pred.append(nb_classifier.predict(terms))
  


In [ ]:
y_pred

['entertainment',
 'business',
 'business',
 'politics',
 'sport',
 'tech',
 'tech',
 'business',
 'entertainment',
 'tech',
 'politics',
 'sport',
 'tech',
 'sport',
 'sport',
 'business',
 'sport',
 'sport',
 'business',
 'entertainment',
 'sport',
 'politics',
 'sport',
 'business',
 'business',
 'business',
 'business',
 'tech',
 'business',
 'politics',
 'sport',
 'sport',
 'business',
 'politics',
 'sport',
 'tech',
 'business',
 'sport',
 'tech',
 'tech',
 'business',
 'tech',
 'sport',
 'business',
 'business',
 'sport',
 'sport',
 'business',
 'tech',
 'sport',
 'politics',
 'tech',
 'entertainment',
 'entertainment',
 'tech',
 'business',
 'business',
 'sport',
 'sport',
 'entertainment',
 'sport',
 'sport',
 'business',
 'sport',
 'business',
 'business',
 'sport',
 'business',
 'tech',
 'sport',
 'sport',
 'sport',
 'business',
 'politics',
 'sport',
 'politics',
 'sport',
 'sport',
 'sport',
 'tech',
 'sport',
 'tech',
 'tech',
 'business',
 'tech',
 'politics',
 'sport',


In [ ]:
y_true

['entertainment',
 'business',
 'business',
 'politics',
 'sport',
 'tech',
 'tech',
 'business',
 'entertainment',
 'tech',
 'politics',
 'sport',
 'tech',
 'sport',
 'sport',
 'business',
 'sport',
 'sport',
 'business',
 'entertainment',
 'entertainment',
 'politics',
 'entertainment',
 'business',
 'business',
 'business',
 'business',
 'tech',
 'business',
 'politics',
 'sport',
 'sport',
 'business',
 'politics',
 'sport',
 'tech',
 'business',
 'politics',
 'tech',
 'tech',
 'business',
 'tech',
 'sport',
 'tech',
 'business',
 'entertainment',
 'tech',
 'business',
 'tech',
 'entertainment',
 'politics',
 'tech',
 'entertainment',
 'entertainment',
 'tech',
 'tech',
 'business',
 'sport',
 'sport',
 'entertainment',
 'entertainment',
 'sport',
 'business',
 'entertainment',
 'business',
 'business',
 'entertainment',
 'business',
 'tech',
 'entertainment',
 'politics',
 'sport',
 'business',
 'politics',
 'sport',
 'politics',
 'sport',
 'politics',
 'entertainment',
 'tech',
 

In [ ]:
from sklearn import metrics

accuracy = metrics.accuracy_score(y_true, y_pred)
precision = metrics.precision_score(y_true, y_pred,average='macro')
recall = metrics.recall_score(y_true, y_pred, average='macro')
f1 = metrics.f1_score(y_true, y_pred, average='macro')

In [ ]:
print("Accuracy of the classifier is : ", accuracy)
print("Precision of the classifier is : ", precision)
print("Recall of the classifier is : ", recall)
print("F1 score of the classifier is : ", f1)

Accuracy of the classifier is :  0.8165548098434005
Precision of the classifier is :  0.8998070964179877
Recall of the classifier is :  0.811872277000688
F1 score of the classifier is :  0.8259328116061919


Improving the classifier:

In [ ]:
#Trying different preprocessing techniques like stemming and lemmatisation on the text
df = pd.read_csv(path)
df

#try applying lemmatisation instead of stemming


ArticleId                                               Text  \
0          1833  worldcom ex-boss launches defence lawyers defe...   
1           154  german business confidence slides german busin...   
2          1101  bbc poll indicates economic gloom citizens in ...   
3          1976  lifestyle  governs mobile choice  faster  bett...   
4           917  enron bosses in $168m payout eighteen former e...   
...         ...                                                ...   
1485        857  double eviction from big brother model caprice...   
1486        325  dj double act revamp chart show dj duo jk and ...   
1487       1590  weak dollar hits reuters revenues at media gro...   
1488       1587  apple ipod family expands market apple has exp...   
1489        538  santy worm makes unwelcome visit thousands of ...   

           Category  
0          business  
1          business  
2          business  
3              tech  
4          business  
...             ...  
1485  entertainment  
1486  entertainment  
1487       business  
1488           tech  
1489           tech  

[1490 rows x 3 columns]

In [ ]:
nltk.download('wordnet')
import nltk
from nltk.stem import WordNetLemmatizer

def lemmatise(words):
  lemmatizer = WordNetLemmatizer()

  # lemmatize the tokens
  lemmatised_words = [lemmatizer.lemmatize(word) for word in words]

  return lemmatised_words



[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [ ]:
#perform preprocessing but lemmatisation this time
for index, row in df.iterrows():
  df.at[index,'Text']=lemmatise(tokenise(clean(row['Text'])))

In [ ]:
df

ArticleId                                               Text  \
0          1833  [worldcom, ex-boss, launch, defence, lawyer, d...   
1           154  [german, business, confidence, slide, german, ...   
2          1101  [bbc, poll, indicates, economic, gloom, citize...   
3          1976  [lifestyle, governs, mobile, choice, faster, b...   
4           917  [enron, boss, $, 168m, payout, eighteen, forme...   
...         ...                                                ...   
1485        857  [double, eviction, big, brother, model, capric...   
1486        325  [dj, double, act, revamp, chart, show, dj, duo...   
1487       1590  [weak, dollar, hit, reuters, revenue, medium, ...   
1488       1587  [apple, ipod, family, expands, market, apple, ...   
1489        538  [santy, worm, make, unwelcome, visit, thousand...   

           Category  
0          business  
1          business  
2          business  
3              tech  
4          business  
...             ...  
1485  entertainment  
1486  entertainment  
1487       business  
1488           tech  
1489           tech  

[1490 rows x 3 columns]

In [ ]:
#Trying differnt train-test splits
from sklearn.model_selection import train_test_split

test_sizes=[0.2,0.3,0.4,0.6,0.8]

for size in test_sizes:
  train_data_2, test_data_2,y1,y2 = train_test_split(df, df , test_size=size, random_state=42)

  #Training the Naive Bayes classifier with TF-ICF:
  nb_classifier = NB(train_data_2)

  #Use the testing set to evaluate the performance of the classifier.
  y_true=[]
  y_pred=[]

  for index, row in test_data_2.iterrows():
    y_true.append(row['Category'])
    terms=row['Text']
    y_pred.append(nb_classifier.predict(terms))

  accuracy = metrics.accuracy_score(y_true, y_pred)
  precision = metrics.precision_score(y_true, y_pred,average='macro')
  recall = metrics.recall_score(y_true, y_pred, average='macro')
  f1 = metrics.f1_score(y_true, y_pred, average='macro')

  print("\n The following metrics for lemmatised data with testing set of size: ", size)
  print("Accuracy of the classifier is : ", accuracy)
  print("Precision of the classifier is : ", precision)
  print("Recall of the classifier is : ", recall)
  print("F1 score of the classifier is : ", f1)

    





 The following metrics for lemmatised data with testing set of size:  0.2
Accuracy of the classifier is :  0.8389261744966443
Precision of the classifier is :  0.8998837045710756
Recall of the classifier is :  0.826535732133933
F1 score of the classifier is :  0.8426597852033295

 The following metrics for lemmatised data with testing set of size:  0.3
Accuracy of the classifier is :  0.8411633109619687
Precision of the classifier is :  0.9001736834256387
Recall of the classifier is :  0.8288198827060675
F1 score of the classifier is :  0.8452449895580199

 The following metrics for lemmatised data with testing set of size:  0.4
Accuracy of the classifier is :  0.7953020134228188
Precision of the classifier is :  0.8866693331545978
Recall of the classifier is :  0.7830187934679664
F1 score of the classifier is :  0.8031401649257808

 The following metrics for lemmatised data with testing set of size:  0.6
Accuracy of the classifier is :  0.7315436241610739
Precision of the classifier 

Observation: For lemmatised data, the accuracy value is maximum when the model has trained with training data of size 0.8 and testing data of 0.2 of the whole dataframe and gets reduced overall as the size of training set reduces, this can be explained as the corpus of training for the model is reduced, the probability of encountering a new word in the training set increases drastically, hence the model is not able to categorise the newer terms and overall the accuracy and other metrics reduce.

When compare the technique stemming and lemmatisation, stemming actually performs much better here as for the training test split of 0.7:0.3 the results of accuracy and other metrics for the stemmed data were much better.

Hence we proceed with the stemmed dataset, and a train test split of 0.7:0.3, since in case of 0.8:0.2, there is a high chance that the model is actually overfitting.

In [ ]:
#Trying using TF-IDF as features

In [ ]:
stemmed_data

Text       Category
0     [worldcom, ex-boss, launch, defenc, lawyer, de...       business
1     [german, busi, confid, slide, german, busi, co...       business
2     [bbc, poll, indic, econom, gloom, citizen, maj...       business
3     [lifestyl, govern, mobil, choic, faster, bette...           tech
4     [enron, boss, $, 168m, payout, eighteen, forme...       business
...                                                 ...            ...
1485  [doubl, evict, big, brother, model, capric, ho...  entertainment
1486  [dj, doubl, act, revamp, chart, show, dj, duo,...  entertainment
1487  [weak, dollar, hit, reuter, revenu, media, gro...       business
1488  [appl, ipod, famili, expand, market, appl, exp...           tech
1489  [santi, worm, make, unwelcom, visit, thousand,...           tech

[1490 rows x 2 columns]

In [ ]:
#using stemmed data and train test split off 0.7:0.3
#ie using train_data and test-data

#We will apply n grams on the stemmed_data (2-3 grams are tested here)
def ngrams(words, n):

    # Create a list to store the n-grams
    n_gram_list = []

    # Iterate over the words 
    for i in range(len(words) - n + 1):
        
        ngram = ' '.join(words[i:i+n])
        
        n_gram_list.append(ngram)

    return n_gram_list



In [ ]:
df_temp=stemmed_data

In [ ]:
#perform 2 gram and 3 gram respectively
for n in range(1,3):

  for index, row in stemmed_data.iterrows():
    df_temp.at[index,'Text']=ngrams(row['Text'], n)

  #split the stemmed_ngram data into 70:30 for train and test purpose
  train_ngram, test_ngram, y1,y2 = train_test_split(df_temp, df_temp , test_size=0.3, random_state=42)

  #Training the Naive Bayes classifier with TF-ICF:
  nb_classifier_ngram = NB(train_ngram)

  #Use the testing set to evaluate the performance of the classifier.
  y_true=[]
  y_pred=[]

  for index, row in test_ngram.iterrows():
    y_true.append(row['Category'])
    terms=row['Text']
    y_pred.append(nb_classifier_ngram.predict(terms))

  accuracy = metrics.accuracy_score(y_true, y_pred)
  precision = metrics.precision_score(y_true, y_pred,average='macro', zero_division= True)
  recall = metrics.recall_score(y_true, y_pred, average='macro', zero_division= True)
  f1 = metrics.f1_score(y_true, y_pred, average='macro', zero_division= True)

  print("\n The following metrics for stemmed data with n grams of n: ",n)
  print("Accuracy of the classifier is : ", accuracy)
  print("Precision of the classifier is : ", precision)
  print("Recall of the classifier is : ", recall)
  print("F1 score of the classifier is : ", f1)







 The following metrics for stemmed data with n grams of n:  1
Accuracy of the classifier is :  0.854586129753915
Precision of the classifier is :  0.907797610554886
Recall of the classifier is :  0.8455814565841141
F1 score of the classifier is :  0.8604158305462652

 The following metrics for stemmed data with n grams of n:  2
Accuracy of the classifier is :  0.22595078299776286
Precision of the classifier is :  0.8451901565995525
Recall of the classifier is :  0.2
F1 score of the classifier is :  0.07372262773722628


However, using bi-grams can also increase the dimensionality of the feature space, which can be a problem if the dataset is small or sparse. In these cases, using bi-grams may actually decrease the accuracy of the model.

In general, it's a good practice to experiment with different feature sets, including unigrams, bi-grams, and other n-grams, and to evaluate the performance of the model with each feature set. This can help determine which feature set is most appropriate for the specific task and dataset.